In [1]:
import math
from scipy.optimize import minimize
import numpy as np

In [2]:
### tools：

def minfunction(f, x0, bounds):
    """
    求一个函数在边界内的最小值
    f：函数
    x0：初始值
    bounds：边界条件。[(min, max),...]
    """
    res = minimize(f, x0, method='SLSQP', bounds=bounds)
    return res

def maxfunction(f, x0, bounds):
    """
    求一个函数在边界内的最大值
    f：函数
    x0：初始值
    bounds：边界条件。[(min, max),...]
    """
    fun = lambda X : -f(X)
    res = minimize(fun, x0, method='SLSQP', bounds=bounds)
    return res


In [3]:
### 目标函数：
bounds = [(-10, 10), (-10, 10), (-10, 10), (-10, 10), (-10, 10), (-10, 10), (-10, 10)]
x_opt = [2.33049935147405174, 1.95137236847114592, -0.477541399510615805, 4.36572624923625874, -0.624486959100388983,
         1.03813099410962173, 1.5942266780671519]
y_opt = 680.630057374402


def G09(X):
    y = (X[0] - 10) ** 2 + 5 * (X[1] - 12) ** 2 + X[2] ** 4 + 3 * (X[3] - 11) ** 2 + 10 * (X[4] ** 6) + 7 * (
                X[5] ** 2) + X[6] ** 4 - 4 * X[5] * X[6] - 10 * X[5] - 8 * X[6]

    g1 = -127 + 2 * X[0] ** 2 + 3 * X[1] ** 4 + X[2] + 4 * X[3] ** 2 + 5 * X[4]
    g2 = -282 + 7 * X[0] + 3 * X[1] + 10 * X[2] ** 3 + X[3] - X[4]
    g3 = -196 + 23 * X[0] + X[1] ** 2 + 6 * X[5] ** 2 - 8 * X[6]
    g4 = 4 * X[0] ** 2 + X[1] ** 2 - 3 * X[0] * X[1] + 2 * X[2] ** 2 + 5 * X[5] - 11 * X[6]

    return y, g1, g2, g3, g4

In [4]:
# y = lambda X: G09(X)[0]
# g1 = lambda X: G09(X)[1]
# g2 = lambda X: G09(X)[2]
# g3 = lambda X: G09(X)[3]
# g4 = lambda X: G09(X)[4]
# x0 = [-10,-10,-10,-10,-10,-10,-10]
# x0 = [0,0,0,0,0,0,0]
# x0 = [10,10,10,10,10,10,10]
# # x0 = [1,2,3,4,5,6,7]

In [5]:
# maxfunction(g4,x0,bounds)

In [6]:
### 适应度函数
def fitnessG09_num(X):
    """
    problem1关于数量惩罚的适应度函数
    X: 对应的解
    epsion：惩罚系数大于fmax-fmin的倍数
    """
    fmax = 1220.174
    fmin = 0.008509619375000003
    count = np.sum(np.array(problem1(X))[1:5]>0)
    
    return -(problem1(X)[0]+epsion*(fmax-fmin)*count)  

def fitnessG09_vio(X):
    """
    problem1关于数量惩罚的适应度函数
    X: 对应的解
    epsion：惩罚系数大于fmax-fmin的倍数
    """
    fmax = 10024263
    fmin = 7
    vmax = 14845
    e = 0.1
    n = 4
    
    res = G09(X)
    fitness = -res[0]
    count = np.sum(np.array(res)[1:5]>0)
    
    if count > 0:
        for i in range(1,len(res)):
            if res[i] > 0:
                cathy = (fmax - fmin)*(e*vmax*n/count+res[i])/(e*vmax)
                fitness = fitness - cathy
    return fitness  


In [ ]:
X = [bounds[i][0] for i in range(len(bounds))]
print(fitnessG09_vio(X))

In [7]:
### PSO
class PSO_fit():
    def __init__(self, pN, dim, max_iter, bounds):
        self.wmax = 0.8 #最大的惯性权重
        self.wmin = 0.4 #最小的惯性权重
        self.c1 = 2  #加速因子
        self.c2 = 2  #加速因子
        self.pN = pN  # 粒子数量
        self.dim = dim  # 搜索维度
        self.max_iter = max_iter  # 迭代次数
        self.bounds = bounds
        
        self.X = np.zeros((self.pN, self.dim))  # 所有粒子的位置：一个pN*dim的矩阵
        self.V = np.zeros((self.pN, self.dim))  # 左右粒子的速度：一个pN*dim的矩阵
        self.pbest = np.zeros((self.pN, self.dim))  # 个体经历的最佳位置：一个pN*dim的矩阵
        self.gbest = np.zeros((self.pN, self.dim))      # 全局最佳位置：一个pN*dim的矩阵
        self.p_fit = np.full(self.pN,-100000000.0)  # 每个个体的历史最佳适应值
        self.g_fit = np.full(self.pN,-100000000.0)    # 全局最佳适应值
    
    def init_Population(self):
        """
        初始化种群
        :return:
        """
        
        for i in range(self.pN):
            for j in range(self.dim):
                self.X[i][j] = self.bounds[j][0] + (self.bounds[j][1] - self.bounds[j][0]) * np.random.random()
                self.V[i][j] = self.bounds[j][0] + (self.bounds[j][1] - self.bounds[j][0]) * np.random.random()
        for i in range(self.pN):
            tmp = fitnessG09_vio(self.X[i])
            if (tmp > self.p_fit[i]):
                self.p_fit[i] = tmp
                self.pbest[i] = self.X[i]
                
        for i in range(self.pN):
            indexes = np.random.randint(low=0,high=self.pN,size=int(self.pN/100))
            for j in indexes:
                if self.p_fit[j] > self.g_fit[i]:
                    self.g_fit[i] = self.p_fit[j]
                    self.gbest[i] = self.pbest[j]

#             self.pbest[i] = self.X[i]
#             tmp = fitnessG01_num(self.X[i])
#             self.p_fit[i] = tmp
#             if (tmp > self.fit):
#                 self.fit = tmp
#                 self.gbest = self.X[i]
        
    def iterator(self):
        """
        迭代
        """
        for t in range(self.max_iter):
            w = self.wmin + (self.wmax - self.wmin) * np.exp(- (4 * t / self.max_iter) * (4 * t / self.max_iter))
            
            for i in range(self.pN):
                self.V[i] = w*self.V[i]+self.c1*np.random.random()*(self.pbest[i]-self.X[i])+self.c2*np.random.random()*(self.gbest[i]-self.X[i])
                self.X[i] = self.X[i] + self.V[i]
                
                """
                控制在搜索范围内
                """ 
                for j in range(self.dim):
                    if self.X[i][j] < self.bounds[j][0]:
                        self.X[i][j] = self.bounds[j][0]
                    if self.X[i][j] > self.bounds[j][1]:
                        self.X[i][j] = self.bounds[j][1]     
            for i in range(self.pN):
                tmp = fitnessG09_vio(self.X[i])
                if (tmp > self.p_fit[i]):
                    self.p_fit[i] = tmp
                    self.pbest[i] = self.X[i]
            for i in range(self.pN):
                indexes = np.random.randint(low=0,high=self.pN,size=int(self.pN/100))
                for j in indexes:
                    if self.p_fit[j] > self.g_fit[i]:
                        self.g_fit[i] = self.p_fit[j]
                        self.gbest[i] = self.pbest[j]
            print(self.g_fit)  
        return self.gbest, self.g_fit

In [8]:
PSO = PSO_fit(pN=1000, dim=7, max_iter=300, bounds=bounds)

In [9]:
PSO.init_Population()

In [10]:
PSO.iterator()

[-4.13378917e+07 -4.01568176e+07 -4.01130349e+07 -4.02271297e+07
 -4.18631758e+07 -4.07474510e+07 -4.03274025e+07 -4.07540141e+07
 -4.08001524e+07 -4.12209054e+07 -2.39943036e+03 -4.17680513e+07
 -1.00047523e+07 -4.30572072e+07 -4.21367346e+07 -4.18015054e+07
 -4.10371312e+07 -4.08246973e+07 -4.93547961e+03 -5.16540801e+05
 -4.13366604e+07 -4.12011447e+07 -4.16530781e+07 -4.22337832e+07
 -4.11519795e+07 -4.12909914e+07 -2.51615201e+06 -4.01568176e+07
 -4.40943979e+07 -4.07255316e+07 -4.07320571e+07 -4.07255316e+07
 -4.12517727e+07 -4.30333312e+07 -4.09012258e+07 -4.02271297e+07
 -4.06015656e+07 -4.07275708e+07 -4.09169927e+07 -4.01399530e+07
 -4.10396953e+07 -4.07255316e+07 -4.08970464e+07 -1.34478650e+04
 -4.35739390e+07 -4.07540141e+07 -2.30513393e+06 -4.11288313e+07
 -4.11805084e+07 -2.51615201e+06 -4.03664447e+07 -4.10849690e+07
 -4.16530781e+07 -4.03642065e+07 -4.07882296e+07 -4.08180043e+07
 -1.46011079e+05 -4.15361123e+07 -4.20125423e+07 -4.33762438e+07
 -4.20437415e+07 -4.22337

[-6.44051151e+03 -9.78578616e+03 -3.23838453e+03 -2.32691118e+03
 -1.44319185e+03 -3.40848211e+03 -3.43740547e+04 -7.10978950e+03
 -3.12293144e+03 -1.53239292e+05 -2.39943036e+03 -4.93547961e+03
 -1.72402762e+03 -4.56593431e+04 -2.52137368e+04 -2.39943036e+03
 -1.10363402e+05 -3.15437041e+03 -3.11916866e+03 -1.52412028e+03
 -1.42360730e+04 -8.82854082e+03 -5.32205278e+03 -3.12293144e+03
 -2.32691118e+03 -1.13874757e+04 -3.15437041e+03 -1.11935261e+04
 -2.13480909e+03 -4.22747537e+03 -2.32691118e+03 -2.38175967e+04
 -1.22913001e+04 -2.16062747e+03 -1.52412028e+03 -1.52412028e+03
 -9.78578616e+03 -2.32691118e+03 -1.52412028e+03 -4.93547961e+03
 -1.42360730e+04 -2.39943036e+03 -6.02611145e+03 -3.40848211e+03
 -5.05708159e+04 -3.11623708e+05 -2.30513393e+06 -1.53239292e+05
 -1.13825630e+04 -1.49713123e+03 -1.00060751e+07 -4.93547961e+03
 -8.65192390e+04 -1.42360730e+04 -3.23838453e+03 -3.12293144e+03
 -1.13161510e+04 -9.78578616e+03 -1.34478650e+04 -9.78578616e+03
 -2.16062747e+03 -6.44051

[ -1483.86698933  -1724.02762282   -983.25700539  -1066.96843759
  -1366.13508884  -1153.25361403  -1366.13508884  -1640.04274224
  -2134.80909154  -1866.44521529  -1524.12028385  -1556.02036884
  -1724.02762282  -1888.82050507  -1659.83774195  -2160.62746863
  -1941.59776012  -1724.02762282  -1483.86698933  -1101.65234161
  -2101.15460546  -1879.55163075  -1483.86698933  -1348.66569427
  -1153.25361403  -1348.66569427  -3154.37040978  -2478.49948875
  -1233.17820926  -3249.02104216  -1443.19185117  -1153.25361403
  -1117.0754733   -1528.40949366  -1524.12028385  -1167.71386949
  -1743.47373802  -1587.58864474  -1524.12028385  -2655.27784438
  -1117.0754733   -1503.31587083  -1117.0754733   -1879.55163075
  -1174.16748323  -2054.389107    -1167.71386949  -1067.65676818
  -1135.15895287  -1167.71386949  -1395.36210809  -1308.29973169
  -1298.89690732  -2326.91118149  -3238.384529    -1174.16748323
  -1067.65676818  -1223.51841829  -3175.35479276  -1443.19185117
  -1260.95355387  -1260.9

[-1003.44930129 -1129.38262646  -983.25700539 -1066.96843759
 -1366.13508884 -1046.23342206 -1366.13508884 -1244.26370272
 -1223.51841829 -1096.80302645 -1293.68839584 -1524.12028385
 -1445.18658207 -1022.68007588 -1283.48500083 -2160.62746863
 -1129.38262646 -1483.86698933 -1483.86698933 -1101.65234161
 -1888.82050507 -1066.96843759 -1483.86698933 -1348.66569427
 -1153.25361403 -1117.0754733  -1095.88619566 -1066.96843759
  -996.23322747  -983.25700539 -1167.71386949  -983.25700539
 -1117.0754733  -1051.06454614 -1153.25361403 -1167.71386949
 -1743.47373802 -1283.48500083  -996.23322747 -1248.24996582
 -1117.0754733  -1503.31587083 -1117.0754733   -983.25700539
 -1167.71386949  -996.23322747 -1167.71386949 -1067.65676818
 -1129.38262646 -1051.06454614 -1167.71386949 -1096.80302645
 -1274.31083413 -1057.7480336  -1435.61687107 -1118.18716388
 -1067.65676818 -1174.16748323  -995.55046322  -996.23322747
 -1023.6276528  -1129.38262646 -1135.15895287 -1224.98968199
 -1244.26370272 -1166.37

[ -878.81488492  -884.52427309  -983.25700539 -1066.96843759
 -1005.50518178 -1007.55212908 -1003.27277518  -998.43066433
 -1075.9798088  -1060.9383159  -1089.68358217  -966.66422993
  -884.52427309 -1004.46696571 -1117.1720751  -1128.43745607
 -1022.68007588 -1224.98968199 -1144.99278936  -897.08794667
 -1005.24140114 -1066.96843759 -1051.06454614 -1003.44930129
 -1017.10579653 -1046.23342206 -1095.88619566  -990.24223925
  -863.73231312  -974.83553511  -969.44344204  -983.25700539
 -1063.07616903 -1004.46696571 -1128.43745607 -1101.65234161
 -1006.20208334  -996.23322747  -996.23322747 -1022.68007588
 -1117.0754733   -892.0784276  -1111.73356872  -969.44344204
 -1066.66903553  -996.23322747 -1007.55212908  -892.88722871
 -1017.10579653 -1051.06454614 -1100.25519997 -1078.0649284
  -884.52427309 -1008.21312881  -852.67030422  -852.67030422
 -1016.82476003  -892.0784276   -995.55046322  -996.23322747
  -966.66422993 -1008.21312881  -995.55046322 -1022.54092429
  -884.52427309 -1117.097

...

[-680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.

[-680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.

[-680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.

[-680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.63005737 -680.63005737 -680.63005737 -680.63005737 -680.63005737
 -680.

(array([[ 2.33049935,  1.95137239, -0.47754132, ..., -0.62448698,
          1.03813105,  1.59422668],
        [ 2.3304994 ,  1.95137239, -0.47754136, ..., -0.62448701,
          1.03813105,  1.59422674],
        [ 2.33049938,  1.95137237, -0.47754136, ..., -0.62448698,
          1.038131  ,  1.5942267 ],
        ...,
        [ 2.33049937,  1.95137238, -0.47754145, ..., -0.62448695,
          1.03813108,  1.59422674],
        [ 2.33049938,  1.95137237, -0.47754139, ..., -0.62448699,
          1.03813102,  1.59422672],
        [ 2.3304994 ,  1.95137236, -0.47754137, ..., -0.62448697,
          1.03813104,  1.59422675]]),
 array([-680.63005737, -680.63005737, -680.63005737, -680.63005737,
        -680.63005737, -680.63005737, -680.63005737, -680.63005737,
        -680.63005737, -680.63005737, -680.63005737, -680.63005737,
        -680.63005737, -680.63005737, -680.63005737, -680.63005737,
        -680.63005737, -680.63005737, -680.63005737, -680.63005737,
        -680.63005737, -680.63005